In [1]:
%pwd

'c:\\Users\\eliza\\CLINICO-Medical-Chatbot\\trials'

In [2]:
import os
os.chdir("../")

In [3]:
%pwd

'c:\\Users\\eliza\\CLINICO-Medical-Chatbot'

In [4]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

c:\Users\eliza\anaconda3\envs\chatbot\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [20]:
def load_pdf_files(data):
    loader = DirectoryLoader(
        data, 
        glob='*.pdf',
        loader_cls=PyPDFLoader
    )

    documents = loader.load()
    return documents

In [21]:
extracted_data = load_pdf_files('data')

In [22]:
extracted_data

[Document(metadata={'producer': 'Acrobat Distiller 4.0 for Macintosh', 'creator': 'Penta Systems International Inc.', 'creationdate': '2006-04-26T07:23:16+02:00', 'subject': "Harrison's Manual of Medicine 16th Edition", 'author': 'Shahram - "Dennis L. Kasper', 'keywords': 'Shahram', 'moddate': '2006-04-27T04:30:41+02:00', 'title': "Harrison's Manual of Medicine 16th Edition", 'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf', 'total_pages': 1104, 'page': 0, 'page_label': 'Cover'}, page_content='40521 Harrison/CompanionHandbook 16/e BATCH LEFT\ntop of rh\nbase of rh\ncap height\nbase of text\nshort\nstand\ndrop folio'),
 Document(metadata={'producer': 'Acrobat Distiller 4.0 for Macintosh', 'creator': 'Penta Systems International Inc.', 'creationdate': '2006-04-26T07:23:16+02:00', 'subject': "Harrison's Manual of Medicine 16th Edition", 'author': 'Shahram - "Dennis L. Kasper', 'keywords': 'Shahram', 'moddate': '2006-04-27T04:30:41+02:00', 'title': "Harrison's Manual of Med

In [23]:
len(extracted_data)

1863

In [24]:
from typing import List
from langchain.schema import Document

def filter_to_minimal_docs(docs: List[Document]) -> List[Document]:
    minimal_docs: List[Document] = []   
    for doc in docs:
        src = doc.metadata.get("source")
        if src:
            doc.metadata["source"] = src.split("/")[-1]
        minimal_docs.append(
            Document(
                page_content=doc.page_content,
                metadata={'source': src}
            )
        )
    return minimal_docs

In [25]:
minimal_docs = filter_to_minimal_docs(extracted_data)

In [26]:
minimal_docs

[Document(metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='40521 Harrison/CompanionHandbook 16/e BATCH LEFT\ntop of rh\nbase of rh\ncap height\nbase of text\nshort\nstand\ndrop folio'),
 Document(metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='HARRISON’S\nManual of\nMedicine\n40521 Harrison/CompanionHandbook 16/e BATCH RIGHT\ntop of rh\nbase of rh\ncap height\nbase of text\nshort\nstand\ndrop folio'),
 Document(metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='EDITORS\nDennis L. Kasper, MD, MA(HON)\nWilliam Ellery Channing Professor of Medicine,\nProfessor of Microbiology and Molecular Genetics,\nHarvard Medical School;\nDirector, Channing Laboratory,\nDepartment of Medicine,\nBrigham and Women’s Hospital, Boston\nEugene Braunwald, MD, MA(HON), MD(HON), ScD(HON)\nDistinguished Hersey Professor of Medicine,\nHarvard Medical School;\nChairman, TIMI Study Group,\nB

In [27]:
def text_split(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=600,
        chunk_overlap=100,
    )
    text_chunks = text_splitter.split_documents(minimal_docs)
    return text_chunks

In [28]:
text_chunks = text_split(minimal_docs)
print(f'Number of text chunks: {len(text_chunks)}')

Number of text chunks: 12631


In [29]:
text_chunks

[Document(metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='40521 Harrison/CompanionHandbook 16/e BATCH LEFT\ntop of rh\nbase of rh\ncap height\nbase of text\nshort\nstand\ndrop folio'),
 Document(metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='HARRISON’S\nManual of\nMedicine\n40521 Harrison/CompanionHandbook 16/e BATCH RIGHT\ntop of rh\nbase of rh\ncap height\nbase of text\nshort\nstand\ndrop folio'),
 Document(metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='EDITORS\nDennis L. Kasper, MD, MA(HON)\nWilliam Ellery Channing Professor of Medicine,\nProfessor of Microbiology and Molecular Genetics,\nHarvard Medical School;\nDirector, Channing Laboratory,\nDepartment of Medicine,\nBrigham and Women’s Hospital, Boston\nEugene Braunwald, MD, MA(HON), MD(HON), ScD(HON)\nDistinguished Hersey Professor of Medicine,\nHarvard Medical School;\nChairman, TIMI Study Group,\nB

In [41]:
import torch
from langchain_community.embeddings import HuggingFaceEmbeddings

def download_embeddings():
    model_name = "BAAI/bge-small-en-v1.5"   
    embeddings = HuggingFaceEmbeddings(
        model_name=model_name,
        model_kwargs={"device": "cuda" if torch.cuda.is_available() else "cpu"}
    )
    return embeddings

embedding = download_embeddings()

In [42]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 512, 'do_lower_case': True}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': True, 'pooling_mode_mean_tokens': False, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='BAAI/bge-small-en-v1.5', cache_folder=None, model_kwargs={'device': 'cpu'}, encode_kwargs={}, multi_process=False, show_progress=False)

In [43]:
vector = embedding.embed_query('Helllo world')
vector

[-0.014819889329373837,
 0.008786682970821857,
 0.0032915796618908644,
 -0.06358318030834198,
 0.021668732166290283,
 -0.03612450882792473,
 0.02615513652563095,
 -0.01377943903207779,
 -0.054318539798259735,
 -0.029019363224506378,
 0.04066337272524834,
 -0.044236090034246445,
 0.03031931258738041,
 0.050979822874069214,
 0.017933443188667297,
 -0.024145426228642464,
 -0.01548625249415636,
 0.004114504437893629,
 -0.09655832499265671,
 -0.02414536103606224,
 0.09582659602165222,
 0.013433792628347874,
 -0.01100871991366148,
 0.018455617129802704,
 -0.023702232167124748,
 0.02069750241935253,
 -0.024270599707961082,
 0.04832611232995987,
 -0.06131364405155182,
 -0.11289966106414795,
 0.019260261207818985,
 -0.027319418266415596,
 0.025826863944530487,
 -0.026159022003412247,
 -0.004154803231358528,
 0.0390031635761261,
 -0.0009739604429341853,
 0.06319866329431534,
 -0.09215972572565079,
 0.04247686639428139,
 0.04017331451177597,
 0.0297701433300972,
 0.007372220046818256,
 -0.0410448

In [44]:
print('Vector Length:', len(vector))

Vector Length: 384


In [45]:
from dotenv import load_dotenv
load_dotenv("c:/Users/eliza/CLINICO-Medical-Chatbot/.env", override=True)

True

In [46]:
PINECONE_API_KEY = os.getenv('PINECONE_API_KEY')
OPENAI_API_KEY = os.getenv('OPENAI_API_KEY')

os.environ['PINECONE_API_KEY'] = PINECONE_API_KEY
os.environ['OPENAI_API_KEY'] = OPENAI_API_KEY

In [47]:
from pinecone import Pinecone
pinecone_api_key = PINECONE_API_KEY

pc = Pinecone(api_key=pinecone_api_key)

In [48]:
pc

In [51]:
from pinecone import Pinecone, ServerlessSpec

index_name = "clinico-chatbot"

if index_name not in [idx["name"] for idx in pc.list_indexes()]:
    pc.create_index(
        name = index_name,
        dimension = 384,
        metric="cosine",
        spec=ServerlessSpec(
            cloud="aws",
            region="us-east-1"
        )
    )

index = pc.Index(index_name)

In [117]:
# from langchain_pinecone import PineconeVectorStore

# docsearch = PineconeVectorStore.from_documents(
#     documents=text_chunks,
#     embedding=embedding,
#     index_name=index_name
# )

In [105]:
from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_existing_index(
    index_name = index_name, 
    embedding = embedding 
)          

In [106]:
base_retriever = docsearch.as_retriever(
    search_type="similarity",
    search_kwargs={"k": 20}
)

In [107]:
from sentence_transformers import CrossEncoder
from langchain.schema import Document
from langchain_core.runnables import RunnableLambda

reranker = CrossEncoder("BAAI/bge-reranker-base")

base_retriever = docsearch.as_retriever(search_kwargs={"k": 20})

def rerank_docs(query, docs, top_k=5):
    pairs = [[query, d.page_content] for d in docs]
    scores = reranker.predict(pairs)
    ranked = sorted(zip(scores, docs), key=lambda x: x[0], reverse=True)
    return [doc for score, doc in ranked[:top_k]]

def rerank_retriever_fn(query):
    if isinstance(query, dict):
        query = query["input"]
    
    docs = base_retriever.invoke(query)
    reranked = rerank_docs(query, docs, top_k=5)
    return reranked

rerank_retriever = RunnableLambda(rerank_retriever_fn)


In [108]:
# Sebelum pakai reranker
retrieved_docs = base_retriever.invoke('What is acne')
retrieved_docs

[Document(id='a2242a57-d20b-4d86-8b9c-6a2e0302d7eb', metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='ACNE\nACNE VULGARIS Usually a self-limited disorder of teenagers and\nyoung adults. Comedones (small cyst formed in hair follicle) are clinical hall-\nmark;oftenaccompaniedbyinﬂammatorylesionsofpapules,pustules,ornod-\nules. May scarin severecases.'),
 Document(id='2452b8da-693c-4c48-b005-21b9d42b28f5', metadata={'source': 'data\\Harrisons.Manual.of_.Medicine.16th.Edition.pdf'}, page_content='sion).\nACNE ROSACEA Inﬂammatory disorder affecting predominantly the\ncentralface,rarelyaffectingpts /H1102130yearsofage.Tendencytowardexaggerated\nﬂushing,witheventualsuperimpositionofpapules,pustules,andtelangiectases.\nMay lead to rhinophyma and ocularproblems.\nTREATMENT\nOral tetracycline, 250–1000 mg/d; topical metronidazole and topical non-\nﬂuorinatedglucocorticoidsmay be useful.\nVASCULAR DISORDERS\nERYTHEMA NODOSUM Septalpanniculitischaracterize

In [109]:
from langchain_openai import ChatOpenAI

chat_model = ChatOpenAI(
    model="gpt-4o", 
    temperature=0
)

In [110]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [111]:
system_prompt = """
You are CLINICO, a medical information assistant. ALWAYS follow these rules:

- You DO NOT provide medical diagnoses, prescriptions, dosages, or definitive treatment advice.
- You provide general medical information, differential contexting (possible causes), and triage recommendations only.
- If the user reports any emergency/red-flag symptoms, immediately respond with a short emergency escalation message telling them to seek urgent care or call emergency services.
- Use an empathetic, clear, non-judgmental tone.
- At the end of every symptom-based reply, include the safety reminder: "This is not a medical diagnosis. See a healthcare professional."

{context}
"""

from langchain.prompts import ChatPromptTemplate

prompt = ChatPromptTemplate.from_messages([
    ("system", system_prompt),
    ("human", "{input}")
])

In [112]:
question_answer_chain = create_stuff_documents_chain(chat_model, prompt)

rag_chain = create_retrieval_chain(
    rerank_retriever,
    question_answer_chain
)


In [113]:
from langchain_community.chat_message_histories import ChatMessageHistory

store = {}

In [114]:
def get_session_history(session_id: str):
    if session_id not in store:
        store[session_id] = ChatMessageHistory()
    return store[session_id]

In [115]:
from langchain_core.runnables.history import RunnableWithMessageHistory

rag_with_memory = RunnableWithMessageHistory(
    rag_chain,
    get_session_history,
    input_messages_key="input",
    history_messages_key="history"
)

In [116]:
response = rag_chain.invoke(
    {"input": "What is Acne?"},
    config={"configurable": {"session_id": "clinico-user"}}
)

print(response["answer"])


Acne, also known as acne vulgaris, is a common skin condition that primarily affects teenagers and young adults, though it can occur at any age. It is characterized by the presence of comedones, which are small cysts formed in hair follicles. These can be open (blackheads) or closed (whiteheads). Acne may also include inflammatory lesions such as papules, pustules, or nodules. In severe cases, acne can lead to scarring.

Acne is often influenced by hormonal changes, which is why it is prevalent during adolescence. Other factors that can contribute to acne include genetics, certain medications, and lifestyle factors. While acne is usually self-limited, meaning it often resolves on its own, it can be persistent and may require treatment to manage symptoms and prevent scarring.

This is not a medical diagnosis. See a healthcare professional.
